In [123]:
import pandas as pd
import numpy as np
import csv

import glob
from datetime import datetime
import time
import os, shlex, subprocess, shutil
import requests
import json

import aiohttp
import asyncio

from tqdm.notebook import tqdm

import gzip

In [7]:
pdb_df = pd.read_csv('pdb_data.csv', header=0, index_col=0)

In [12]:
current_entries_api = "https://data.rcsb.org/rest/v1/holdings/current/entry_ids"
obsolete_entries_api = "https://data.rcsb.org/rest/v1/holdings/removed/entry_ids"

In [13]:
all_current_entries = requests.get(current_entries_api).json()
all_current_entries = [i.lower() for i in all_current_entries]

all_obsolete_entries = requests.get(obsolete_entries_api).json()
all_obsolete_entries = [i.lower() for i in all_obsolete_entries]

In [34]:
pdb_df['status'] = "Current"
pdb_df.loc[pdb_df.pdb_id.isin(all_obsolete_entries), 'status'] = "Obsolete"

In [39]:
pdb_df.to_csv('pdb_data.csv')

In [ ]:
all_json_dict = {}

for c in all_current_entries:
    print(c)
    api_url = f"https://data.rcsb.org/rest/v1/core/entry/{c}"
    all_json_dict[c.lower()] = requests.get(api_url).json()

In [18]:
all_json_dict = {}

async def main():
    async with aiohttp.ClientSession() as session:
        for i, c in enumerate(all_current_entries):
            if i % 1000 == 0:
                print(f"{i}/{len(all_current_entries)} {datetime.now()}")
                
            api_url = f"https://data.rcsb.org/rest/v1/core/entry/{c}"
            async with session.get(api_url) as resp:
                all_json_dict[c.lower()] = await resp.json()

await main()

0/198165 2022-11-21 09:41:51.415240
1000/198165 2022-11-21 09:44:25.608980
2000/198165 2022-11-21 09:47:00.668207
3000/198165 2022-11-21 09:49:35.094194
4000/198165 2022-11-21 09:52:09.232925
5000/198165 2022-11-21 09:54:43.626372
6000/198165 2022-11-21 09:57:17.893634
7000/198165 2022-11-21 09:59:54.651417
8000/198165 2022-11-21 10:02:29.653662
9000/198165 2022-11-21 10:05:04.561976
10000/198165 2022-11-21 10:07:39.381142
11000/198165 2022-11-21 10:10:14.759095
12000/198165 2022-11-21 10:12:49.237106
13000/198165 2022-11-21 10:15:24.145047
14000/198165 2022-11-21 10:17:58.760828
15000/198165 2022-11-21 10:20:33.185976
16000/198165 2022-11-21 10:23:08.235290
17000/198165 2022-11-21 10:25:42.911032
18000/198165 2022-11-21 10:28:17.179945
19000/198165 2022-11-21 10:30:51.640161
20000/198165 2022-11-21 10:33:26.403901
21000/198165 2022-11-21 10:36:01.380166
22000/198165 2022-11-21 10:38:36.292799
23000/198165 2022-11-21 10:41:11.029603
24000/198165 2022-11-21 10:43:45.569693
25000/198165 

In [43]:
all_json_dict

{'190l': {'audit_author': [{'name': 'Zhang, X.-J.', 'pdbx_ordinal': 1},
   {'name': 'Matthews, B.W.', 'pdbx_ordinal': 2}],
  'cell': {'angle_alpha': 90.0,
   'angle_beta': 90.0,
   'angle_gamma': 120.0,
   'length_a': 60.6,
   'length_b': 60.6,
   'length_c': 95.8,
   'zpdb': 6},
  'citation': [{'country': 'NE',
    'id': 'primary',
    'journal_abbrev': 'Biophys.Chem.',
    'journal_id_astm': 'BICIAZ',
    'journal_id_csd': '0829',
    'journal_id_issn': '0301-4622',
    'journal_volume': '101-102',
    'page_first': '43',
    'page_last': '56',
    'pdbx_database_id_doi': '10.1016/S0301-4622(02)00193-X',
    'pdbx_database_id_pub_med': 12487988,
    'rcsb_authors': ['Zhang, X.J.', 'Baase, W.A.', 'Matthews, B.W.'],
    'rcsb_is_primary': 'Y',
    'rcsb_journal_abbrev': 'Biophys Chem',
    'title': 'A helix initiation signal in T4 lysozyme identified by polyalanine mutagenesis.',
    'year': 2002},
   {'country': 'UK',
    'id': '1',
    'journal_abbrev': 'J.Mol.Biol.',
    'journal_id

In [19]:
with open("sample.json", "w") as f:
    json.dump(all_json_dict, f)

In [20]:
with open('sample.json', 'r') as f:
    read_json_dict = json.loads(f.read())

In [21]:
len(read_json_dict)

198165

In [24]:
read_json_dict.keys()

dict_keys(['190l', '1r0w', '2i4r', '3c1x', '3szt', '4ltk', '5f67', '5w1q', '6mx8', '7d8p', '100d', '1qum', '2hy9', '3bw4', '3su2', '4lnm', '5ezy', '5vvn', '6mre', '7d2j', '8gpt', '1a2c', '1r3t', '2i7v', '3c4z', '3t2s', '4lwf', '5f97', '5w4m', '6n0q', '7dbo', '1a7y', '1ra5', '2ies', '3cax', '3t8l', '4m2a', '5ff1', '5wad', '6n6m', '7dhz', '142d', '1qxq', '2i1f', '3bz5', '3swx', '4lqp', '5f2y', '5vyp', '6mua', '7d5l', '8xia', '1a56', '1r6q', '2ibn', '3c81', '3t5m', '4lzd', '5fc2', '5w7e', '6n3o', '7der', '1ab7', '1rd5', '2ihz', '3cdt', '3tbh', '4m59', '5fhy', '5wdg', '6n9e', '7dlb', '1aer', '1rg3', '2ilz', '3cgs', '3tel', '4m85', '5fks', '5wgl', '6ncr', '7dou', '1aho', '1rj6', '2ipi', '3cjp', '3thc', '4mb4', '5fnr', '5wjj', '6nfl', '7drx', '1akj', '1rm8', '2itl', '3cmm', '3tk5', '4me5', '5fqm', '5wmf', '6nig', '7duu', '1anr', '1rpn', '2iwk', '3cpg', '3tn5', '4mhd', '5fts', '5wpq', '6nl9', '7dxr', '1aqt', '1rsy', '2izg', '3cse', '3tq3', '4mkb', '5fwn', '5wsn', '6no7', '7e0w', '1aty', '1rw1

In [67]:
with gzip.open("/datasets/pdb/structures/divided/mmCIF/kl/1kl1.cif.gz", "rt") as f:
    raw_data = f.read()
    
print(raw_data)

data_1KL1
# 
_entry.id   1KL1 
# 
_audit_conform.dict_name       mmcif_pdbx.dic 
_audit_conform.dict_version    5.279 
_audit_conform.dict_location   http://mmcif.pdb.org/dictionaries/ascii/mmcif_pdbx.dic 
# 
loop_
_database_2.database_id 
_database_2.database_code 
PDB   1KL1         
RCSB  RCSB015067   
WWPDB D_1000015067 
# 
loop_
_pdbx_database_related.db_name 
_pdbx_database_related.db_id 
_pdbx_database_related.details 
_pdbx_database_related.content_type 
PDB 1KKJ '1KKJ is the native protein ( without substrate)'                   unspecified 
PDB 1KKP '1KKP is SHMT complexed with Serine substrate'                      unspecified 
PDB 1KL2 '1KL2 is SHMT complexed with glycine and 5-formyl tetrahydrofolate' unspecified 
# 
_pdbx_database_status.status_code                     REL 
_pdbx_database_status.entry_id                        1KL1 
_pdbx_database_status.recvd_initial_deposition_date   2001-12-11 
_pdbx_database_status.deposit_site                    RCSB 
_pdbx_database_

In [60]:
from Bio.PDB.MMCIF2Dict import MMCIF2Dict

def read_cif(file_path):
    f_handle = gzip.open(file_path, 'rt')
    
    return MMCIF2Dict(f_handle)

In [61]:
pdb_dict = read_cif("/datasets/pdb/structures/divided/mmCIF/kl/1kll.cif.gz")

In [62]:
file_path

{'data_': '1KLL',
 '_entry.id': ['1KLL'],
 '_audit_conform.dict_name': ['mmcif_pdbx.dic'],
 '_audit_conform.dict_version': ['5.351'],
 '_audit_conform.dict_location': ['http://mmcif.pdb.org/dictionaries/ascii/mmcif_pdbx.dic'],
 '_database_2.database_id': ['PDB', 'RCSB', 'WWPDB'],
 '_database_2.database_code': ['1KLL', 'RCSB015083', 'D_1000015083'],
 '_database_2.pdbx_database_accession': ['pdb_00001kll', '?', '?'],
 '_database_2.pdbx_DOI': ['10.2210/pdb1kll/pdb', '?', '?'],
 '_pdbx_database_related.db_name': ['PDB'],
 '_pdbx_database_related.db_id': ['1KMZ'],
 '_pdbx_database_related.details': ['the same uncomplexed protein'],
 '_pdbx_database_related.content_type': ['unspecified'],
 '_pdbx_database_status.status_code': ['REL'],
 '_pdbx_database_status.entry_id': ['1KLL'],
 '_pdbx_database_status.recvd_initial_deposition_date': ['2001-12-12'],
 '_pdbx_database_status.deposit_site': ['RCSB'],
 '_pdbx_database_status.process_site': ['RCSB'],
 '_pdbx_database_status.status_code_sf': ['REL

In [56]:
{(k) for k, v in pdb_dict.items() if k.startswith("_atom_site.")}

['_atom_site.group_PDB',
 '_atom_site.id',
 '_atom_site.type_symbol',
 '_atom_site.label_atom_id',
 '_atom_site.label_alt_id',
 '_atom_site.label_comp_id',
 '_atom_site.label_asym_id',
 '_atom_site.label_entity_id',
 '_atom_site.label_seq_id',
 '_atom_site.pdbx_PDB_ins_code',
 '_atom_site.Cartn_x',
 '_atom_site.Cartn_y',
 '_atom_site.Cartn_z',
 '_atom_site.occupancy',
 '_atom_site.B_iso_or_equiv',
 '_atom_site.pdbx_formal_charge',
 '_atom_site.auth_seq_id',
 '_atom_site.auth_comp_id',
 '_atom_site.auth_asym_id',
 '_atom_site.auth_atom_id',
 '_atom_site.pdbx_PDB_model_num']

In [92]:
pdb_dict = read_cif("/datasets/pdb/structures/divided/mmCIF/kl/1kll.cif.gz")

def cif_to_list(file_path):
    
    atom_list = []

    if file_path[-2:] == 'gz':
        f_handle = gzip.open(file_path, 'rt')
        pdb_dict = MMCIF2Dict(f_handle)

    else:
        pdb_dict = MMCIF2Dict(file_path)

    for i in range(len(pdb_dict['_atom_site.group_PDB'])):
        i_dict = {}
        for k in pdb_dict.keys():
            if k.startswith("_atom_site."):
                i_dict[k] = pdb_dict[k][i]

        if i_dict['_atom_site.group_PDB'] == 'ATOM':
            atom_list.append(i_dict)
            
    return atom_list

In [95]:
pdb_list = cif_to_list("/datasets/pdb/interfaces/mmCIF/kl/1kl2_A_B.cif")

In [113]:
with gzip.open('sifts_data/pdb_chain_pfam.csv.gz', 'rt') as f:
    raw_data = [i.strip("\n").split(",") for i in f.readlines()[2:]]

In [116]:
pfam_ids = sorted(list(set([i[3] for i in raw_data])))

In [118]:
len(pfam_ids)

10282

In [124]:
all_json_dict = {}

async def main():
    async with aiohttp.ClientSession() as session:
        for i, c in enumerate(pfam_ids):
            if i % 1000 == 0:
                print(f"{i}/{len(all_current_entries)} {datetime.now()}")
                
            api_url = f"https://www.ebi.ac.uk/interpro/api/structure/PDB/entry/pfam/{c}?format=json"
            async with session.get(api_url) as resp:
                all_json_dict[c.lower()] = await resp.json()

await main()

0/198165 2022-11-30 10:57:35.871532
1000/198165 2022-11-30 10:59:59.160953
2000/198165 2022-11-30 11:02:24.812254
3000/198165 2022-11-30 11:04:41.364107
4000/198165 2022-11-30 11:06:42.402075
5000/198165 2022-11-30 11:08:25.683075
6000/198165 2022-11-30 11:10:14.469063
7000/198165 2022-11-30 11:11:57.649977
8000/198165 2022-11-30 11:13:39.125954
9000/198165 2022-11-30 11:15:22.477399
10000/198165 2022-11-30 11:17:04.494774


In [127]:
with open("pfam_data.json", "w") as f:
    json.dump(all_json_dict, f)

In [128]:
with open('pfam_data.json', 'r') as f:
    pfam_data_json = json.loads(f.read())

In [132]:
pfam_data_json['pf00001']

{'count': 757,
 'next': 'https://www.ebi.ac.uk/interpro/api/structure/PDB/entry/pfam/PF00001?cursor=source%3As%3A1u19&format=json',
 'previous': None,
 'results': [{'metadata': {'accession': '1eds',
    'name': 'SOLUTION STRUCTURE OF INTRADISKAL LOOP 1 OF BOVINE RHODOPSIN (RHODOPSIN RESIDUES 92-123)',
    'source_database': 'pdb',
    'experiment_type': 'nmr',
    'resolution': None},
   'entries': [{'accession': 'PF00001',
     'entry_protein_locations': [{'fragments': [{'start': 55,
         'end': 306,
         'dc-status': 'CONTINUOUS'}],
       'model': 'PF00001',
       'score': 3.9e-46}],
     'protein_length': 348,
     'source_database': 'pfam',
     'entry_type': 'family',
     'entry_integrated': 'ipr000276',
     'chain': 'A',
     'protein': 'p02699',
     'structure_protein_locations': [{'fragments': [{'start': 93,
         'end': 123}]}],
     'protein_structure_mapping': {'A': [{'protein_start': 93,
        'protein_end': 123,
        'structure_start': 1,
        'stru

In [136]:
int_df = pd.read_csv('interface_data.csv', index_col=0)

In [140]:
all_chains = set(list(int_df.chain_1) + list(int_df.chain_2))

In [141]:
len(all_chains)

3367

In [145]:
sorted(list([str(i) for i in all_chains]))

['0',
 '00',
 '01',
 '02',
 '03',
 '04',
 '05',
 '06',
 '07',
 '09',
 '0A',
 '0B',
 '0C',
 '0D',
 '0E',
 '0F',
 '0G',
 '0H',
 '0I',
 '0J',
 '0K',
 '0L',
 '0M',
 '0N',
 '0O',
 '0P',
 '0Q',
 '0R',
 '0S',
 '0U',
 '0V',
 '0W',
 '0X',
 '0Y',
 '0Z',
 '0a',
 '0b',
 '0c',
 '0d',
 '0e',
 '0f',
 '0g',
 '0h',
 '0i',
 '0j',
 '0k',
 '0l',
 '1',
 '10',
 '10a',
 '11',
 '111',
 '12',
 '13',
 '14',
 '15',
 '16',
 '17',
 '18',
 '19',
 '1A',
 '1B',
 '1C',
 '1D',
 '1E',
 '1F',
 '1G',
 '1H',
 '1I',
 '1J',
 '1K',
 '1L',
 '1M',
 '1N',
 '1O',
 '1P',
 '1Q',
 '1R',
 '1S',
 '1T',
 '1U',
 '1V',
 '1W',
 '1X',
 '1Y',
 '1Z',
 '1a',
 '1b',
 '1c',
 '1d',
 '1e',
 '1f',
 '1g',
 '1h',
 '1i',
 '1j',
 '1k',
 '1l',
 '1m',
 '1n',
 '1o',
 '1p',
 '1q',
 '1r',
 '1s',
 '1t',
 '1u',
 '1v',
 '1w',
 '1x',
 '1y',
 '1z',
 '2',
 '20',
 '21',
 '22',
 '222',
 '23',
 '24',
 '25',
 '26',
 '27',
 '28',
 '29',
 '2A',
 '2B',
 '2C',
 '2D',
 '2E',
 '2F',
 '2G',
 '2H',
 '2I',
 '2J',
 '2K',
 '2L',
 '2M',
 '2N',
 '2O',
 '2P',
 '2Q',
 '2R',
 '2S',

In [142]:
def rgb_to_hex(rgb):
    return '#%02x%02x%02x' % rgb

In [146]:
rgb_list = [(123, 104, 238), 
 (240, 128, 128), 
 (143, 188, 143), 
 (222, 184, 135), 
 (255, 127, 80), 
 (128, 128, 128), 
 (107, 142, 35), 
 (100, 100, 100),
 (52, 231, 123),
 (55, 19, 112),
 (255, 255, 150),
 (202, 62, 94),
 (205, 145, 63),
 (183, 118, 231),
 (110, 251, 201),
 (175, 155, 50),
 (105, 205, 48),
 (37, 70, 25),
 (121, 33, 135),
 (83, 140, 208),
 (0, 154, 37),
 (178, 220, 205),
 (255, 152, 213),
 (200, 90, 174),
 (175, 200, 74),
 (63, 25, 12),
 (87, 87, 87),
 (129, 215, 234),
 (102, 242, 126),
 (29, 105, 20),
 (129, 74, 25),
 (129, 38, 192),
 (160, 160, 160),
 (129, 197, 122),
 (157, 175, 255),
 (41, 208, 208)]

In [147]:
hex_list = [rgb_to_hex(i) for i in rgb_list]

In [148]:
hex_list

['#7b68ee',
 '#f08080',
 '#8fbc8f',
 '#deb887',
 '#ff7f50',
 '#808080',
 '#6b8e23',
 '#646464',
 '#34e77b',
 '#371370',
 '#ffff96',
 '#ca3e5e',
 '#cd913f',
 '#b776e7',
 '#6efbc9',
 '#af9b32',
 '#69cd30',
 '#254619',
 '#792187',
 '#538cd0',
 '#009a25',
 '#b2dccd',
 '#ff98d5',
 '#c85aae',
 '#afc84a',
 '#3f190c',
 '#575757',
 '#81d7ea',
 '#66f27e',
 '#1d6914',
 '#814a19',
 '#8126c0',
 '#a0a0a0',
 '#81c57a',
 '#9dafff',
 '#29d0d0']

In [149]:
from Bio.PDB.MMCIF2Dict import MMCIF2Dict

In [150]:
def cif_to_dict(file_path):

    if file_path[-2:] == 'gz':
        f_handle = gzip.open(file_path, 'rt')
        return MMCIF2Dict(f_handle)

    else:
        return MMCIF2Dict(file_path)

In [164]:
struct_dict = cif_to_dict("/datasets/pdb/structures/divided/mmCIF/j3/3j3q.cif.gz")

In [165]:
chain_list = sorted(list(set(struct_dict['_atom_site.auth_asym_id'])))

In [166]:
color_list = ['#7b68ee', '#f08080', '#8fbc8f', '#deb887', '#ff7f50', '#808080', '#6b8e23',
              '#646464', '#34e77b', '#371370', '#ffff96', '#ca3e5e', '#cd913f', '#b776e7',
              '#6efbc9', '#af9b32', '#69cd30', '#254619', '#792187', '#538cd0', '#009a25',
              '#b2dccd', '#ff98d5', '#c85aae', '#afc84a', '#3f190c', '#575757', '#81d7ea',
              '#66f27e', '#1d6914', '#814a19', '#8126c0', '#a0a0a0', '#81c57a', '#9dafff', '#29d0d0']

In [167]:
color_dict = {chain_list[k]: color_list[k % len(color_list)] for k in range(len(chain_list))}

In [168]:
color_dict

{'0': '#7b68ee',
 '1': '#f08080',
 '10': '#8fbc8f',
 '11': '#deb887',
 '12': '#ff7f50',
 '13': '#808080',
 '14': '#6b8e23',
 '15': '#646464',
 '16': '#34e77b',
 '17': '#371370',
 '18': '#ffff96',
 '19': '#ca3e5e',
 '1A': '#cd913f',
 '1B': '#b776e7',
 '1C': '#6efbc9',
 '1D': '#af9b32',
 '1E': '#69cd30',
 '1F': '#254619',
 '1G': '#792187',
 '1H': '#538cd0',
 '1I': '#009a25',
 '1J': '#b2dccd',
 '1K': '#ff98d5',
 '1L': '#c85aae',
 '1M': '#afc84a',
 '1N': '#3f190c',
 '1O': '#575757',
 '1P': '#81d7ea',
 '1Q': '#66f27e',
 '1R': '#1d6914',
 '1S': '#814a19',
 '1T': '#8126c0',
 '1U': '#a0a0a0',
 '1V': '#81c57a',
 '1W': '#9dafff',
 '1X': '#29d0d0',
 '1Y': '#7b68ee',
 '1Z': '#f08080',
 '1a': '#8fbc8f',
 '1b': '#deb887',
 '1c': '#ff7f50',
 '1d': '#808080',
 '1e': '#6b8e23',
 '1f': '#646464',
 '1g': '#34e77b',
 '1h': '#371370',
 '1i': '#ffff96',
 '1j': '#ca3e5e',
 '1k': '#cd913f',
 '1l': '#b776e7',
 '1m': '#6efbc9',
 '1n': '#af9b32',
 '1o': '#69cd30',
 '1p': '#254619',
 '1q': '#792187',
 '1r': '#538